In [1]:
import tensorflow as tf
import dlib
import cv2
import os
import numpy as np
import pandas as pd
from PIL import Image, ImageChops, ImageEnhance
from tensorflow.keras.models import load_model
from tensorflow.keras.preprocessing.image import img_to_array, load_img
from IPython.display import HTML
from base64 import b64encode

In [2]:
model = load_model('test_model.hdf5')

In [3]:
def play_video(folder, video_file, subset):
    video_url = open(os.path.join(folder, subset, video_file),'rb').read()
    data_url = "data:video/mp4;base64," + b64encode(video_url).decode()
    return HTML("""<video width=500 controls><source src="%s" type="video/mp4"></video>""" % data_url)

In [4]:
DATA_FOLDER = ''
TRAIN_SAMPLE_FOLDER = 'train_sample_videos'
TEST_DATA_FOLDER = ''
TEST_FOLDER = 'test_videos'
train_sample_metadata = pd.read_json(os.path.join(DATA_FOLDER, TRAIN_SAMPLE_FOLDER, 'metadata.json')).T
fake_train_sample_video = list(train_sample_metadata.loc[train_sample_metadata.label=='FAKE'].index)
real_train_sample_video = list(train_sample_metadata.loc[train_sample_metadata.label=='REAL'].index)

In [12]:
input_shape = (128, 128, 3)
pr_data = []
detector = dlib.cnn_face_detection_model_v1('mmod_human_face_detector.dat')
test_video = np.random.choice(fake_train_sample_video)
cap = cv2.VideoCapture('train_sample_videos/' + test_video)
frameRate = cap.get(5)
pred = []
while cap.isOpened():
    frameId = cap.get(1)
    ret, frame = cap.read()
    if ret != True:
        break
    if frameId % ((int(frameRate)+1)*1) == 0:
        face_rects = detector(frame, 1)
        for i, d in enumerate(face_rects):
            x1 = d.rect.left()
            y1 = d.rect.top()
            x2 = d.rect.right()
            y2 = d.rect.bottom()
            crop_img = frame[y1:y2, x1:x2]
            data = img_to_array(cv2.resize(crop_img, (128, 128))).flatten() / 255.0
            data = data.reshape(-1, 128, 128, 3)
            pred.append(np.argmax(model.predict(data),axis=1))
print("Real" if sum(pred)/len(pred) > 0.5 else "Fake")
play_video(DATA_FOLDER, test_video, TRAIN_SAMPLE_FOLDER)

Real
